In [1]:
import folium
import pandas as pd
from bs4 import BeautifulSoup
#import pickle
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait  # for implicit and explict waits
from selenium.webdriver.chrome.options import Options  # for suppressing the browser

In [2]:
chrome_driver_path = 'C:\drivers\chromedriver.exe'
url = "https://m.le360.ma/covidmaroc/"
option = webdriver.ChromeOptions()
option.add_argument('headless')
browser = webdriver.Chrome(chrome_driver_path,options=option)
browser.get(url)
html = browser.page_source
browser.quit()

In [3]:
'''outfile = open('html_save','wb')
pickle.dump(html,outfile)
outfile.close()'''
'''infile = open('html_save','rb')
html = pickle.load(infile)
infile.close()'''

"infile = open('html_save','rb')\nhtml = pickle.load(infile)\ninfile.close()"

In [4]:
soup = BeautifulSoup(html,'html.parser')
list_table=soup.find_all('table', class_='table table-bordered dataTable')[0].find('tbody').find_all('tr')

In [5]:
def clean_word(L):
    a=[]
    for word in L:
        if len(word)>2:
            a.append(word)
    return " ".join(a)

In [6]:
mytable=[]
for row in list_table:
    row=row.find_all('td')
    name = clean_word(row[0].find('span').text.split(' ')).split('\u200b')[0]
    
    if(row[1].text==''):
        cas=0
    else:
        cas = int(row[1].text)

    if(row[2].text[1:]==''):
        cast_24=0
    else:
        cast_24 = int(row[2].text[1:])
        
    if(row[3].text[1:]==''):
        dead_24=0
    else:
        dead_24 = int(row[3].text[1:])
    mytable.append({'name': name , 'cas': cas , 'cas_24': cast_24, 'dead_24':dead_24 })

In [7]:
mytable

[{'name': 'Grand Casablanca-Settat',
  'cas': 21728,
  'cas_24': 1133,
  'dead_24': 16},
 {'name': 'Rabat Salé Kenitra', 'cas': 11409, 'cas_24': 538, 'dead_24': 6},
 {'name': 'Souss-Massa', 'cas': 6154, 'cas_24': 288, 'dead_24': 5},
 {'name': 'Tanger Tetouan Hoceima', 'cas': 4923, 'cas_24': 266, 'dead_24': 2},
 {'name': 'Marrakech Safi', 'cas': 4557, 'cas_24': 286, 'dead_24': 5},
 {'name': 'Oriental', 'cas': 2672, 'cas_24': 108, 'dead_24': 6},
 {'name': 'Guelmim Oued Noun', 'cas': 1541, 'cas_24': 68, 'dead_24': 1},
 {'name': 'Laâyoune-Sakia Hamra', 'cas': 1419, 'cas_24': 78, 'dead_24': 0},
 {'name': 'Fès meknes', 'cas': 1328, 'cas_24': 100, 'dead_24': 3},
 {'name': 'Beni Mellal-Khénifra', 'cas': 1081, 'cas_24': 87, 'dead_24': 2},
 {'name': 'Darâa-Tafilalet', 'cas': 886, 'cas_24': 56, 'dead_24': 4},
 {'name': 'Dakhla-Oued Daha', 'cas': 360, 'cas_24': 27, 'dead_24': 0}]

In [8]:
regions_loc = [{'name': 'Oriental',
  'latitude': 34.21063161705621,
  'longitude': -2.2398292872475123},
 {'name': 'Tanger Tetouan Al Hoceima',
  'latitude': 35.21648916999964,
  'longitude': -5.46061811161441},
 {'name': 'Guelmim Oued Noun',
  'latitude': 28.537079417694862,
  'longitude': -10.21129615427537},
 {'name': 'Dakhla-Oued Ed Daha',
  'latitude': 23.187768662138904,
  'longitude': -14.576887039381933},
 {'name': 'Beni Mellal-Khénifra',
  'latitude': 32.35536866706775,
  'longitude': -6.354611221480209},
 {'name': 'Darâa-Tafilalet',
  'latitude': 30.849663419282095,
  'longitude': -5.281174310301617},
 {'name': 'Marrakech Safi',
  'latitude': 31.658566001930208,
  'longitude': -8.50060605705501},
 {'name': 'Grand Casablanca-Settat',
  'latitude': 33.09434328504623,
  'longitude': -7.5835225431320215},
 {'name': 'Fès meknes',
  'latitude': 33.81997585277711,
  'longitude': -4.635183604212562},
 {'name': 'Laâyoune-Sakia El Hamra',
  'latitude': 26.150695319294833,
  'longitude': -12.827810335977418},
 {'name': 'Rabat Salé Kenitra',
  'latitude': 34.03819378608868,
  'longitude': -6.373051694854541},
 {'name': 'Souss-Massa',
  'latitude': 29.911104363087805,
  'longitude': -8.683976891847944}]

In [9]:
L=[]
for i in range(12):
    for j in range(12):
        if(regions_loc[i]['name'][0:5]==mytable[j]['name'][0:5]):
            mytable[j]['name'] = regions_loc[i]['name']
            mytable[j]['latitude'] = regions_loc[i]['latitude']
            mytable[j]['longitude'] = regions_loc[i]['longitude']
            L.append(mytable[j])
            continue

In [10]:
df = pd.DataFrame(L)
df

name    cas  cas_24  dead_24   latitude  longitude
0                    Oriental   2672     108        6  34.210632  -2.239829
1   Tanger Tetouan Al Hoceima   4923     266        2  35.216489  -5.460618
2           Guelmim Oued Noun   1541      68        1  28.537079 -10.211296
3         Dakhla-Oued Ed Daha    360      27        0  23.187769 -14.576887
4        Beni Mellal-Khénifra   1081      87        2  32.355369  -6.354611
5             Darâa-Tafilalet    886      56        4  30.849663  -5.281174
6              Marrakech Safi   4557     286        5  31.658566  -8.500606
7     Grand Casablanca-Settat  21728    1133       16  33.094343  -7.583523
8                  Fès meknes   1328     100        3  33.819976  -4.635184
9     Laâyoune-Sakia El Hamra   1419      78        0  26.150695 -12.827810
10         Rabat Salé Kenitra  11409     538        6  34.038194  -6.373052
11                Souss-Massa   6154     288        5  29.911104  -8.683977

In [11]:
ma = folium.Map(location=[30, -10], zoom_start=5, min_zoom=4, max_zoom=7,tiles="cartodbpositron")
geo = "https://raw.githubusercontent.com/Salah-Zkara/Morocco-GeoJson/master/Morocco-Regions.json"
folium.Choropleth(
    geo_data=geo,
    name='COVID-19',
    data=df,
    columns=['name', 'cas'],
    key_on='feature.properties.nom_region',
    fill_color='OrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Total de cas confirmé',
).add_to(ma)

In [12]:
def plotDot(point):
    html ="<center>"+str(point['name'])+"</center>"+"<br>"+"<font color='#d95e00'>"+"<b>"+str(point['cas'])+"</b>"+"</font>"+" Total de cas confirmé.<br>"+"<font color='#e6b01c'>"+"<b>"+str(point['cas_24'])+"</b>"+"</font>"+" Cas contaminés aujourd'hui.<br>"+"<font color='#cc0c0c'>"+"<b>"+str(point['dead_24'])+"</b>"+"</font>"+" Décès aujourd'hui.<br>"
    iframe = folium.IFrame(html,
                       width=250,
                       height=120)
    folium.CircleMarker(location=[point.latitude, point.longitude],
                        radius=24,
                        weight=0,
                        popup = folium.Popup(iframe),
                        fill_color='#000000',
                        fill_opacity=0,
                        line_opacity=0
                       ).add_to(ma)

df.apply(plotDot, axis = 1)

ma.fit_bounds(ma.get_bounds())

In [13]:
ma

In [14]:
ma.save(outfile= "Covid-Map-Morocco.html")